In [1]:
import os
os.chdir('/home/xyz/data/haoyan/bandits')

import bandits as bd
import numpy as np

In [2]:
c = np.array([1,2,2,4,4,6,3,7,5,5]) / 10
a = np.array([[4,4,4,4], [1,1,1,1], [8,8,8,8], [6,6,6,6], [3,7,3,7], [2,9,2,9], [5,3,5,3], [8,1,8,1], [6,2,6,2], [7,3.6,7,3.6]])

def f(vec):
    return sum(1 / (((a - vec)**2).sum(axis=1) + c))


def g(u, v, x, y):
    return f(np.array([u, v, x, y]))

In [3]:
g(4,4,4,4)

10.536283726219603

In [6]:
import plotly.graph_objects as go

x = np.linspace(0, 10, 200)
y = np.linspace(0, 10, 200)

z = []
for yy in y:
    zz = []
    for xx in x:
        zz.append(f([xx, yy]))
    z.append(zz)
    
fig = go.Figure(data=[go.Surface(z=z, x=x, y=y)])

fig.update_layout(autosize=False,
                  width=1000, height=500,
                  scene_camera_eye=dict(x=1, y=4, z=2),
                  margin=dict(l=1, r=1, b=1, t=1))

fig.show()


ValueError: operands could not be broadcast together with shapes (10,4) (2,) 

In [4]:
n_trials = 5000
n_experiment = 5
vec = list(range(0, 11))
bound = (0, 10)

In [9]:
params_list_dict = {
    'u': vec,
    'v': vec,
}

pbounds={
    'x': bound,
    'y': bound,
}

scores_list = []
actions_list = []

def single_func(n, file):
    bandit = bd.GaussianBandit(
        g,
        params_list_dict=params_list_dict,
        pbounds=pbounds,
        random_state=n*128,
        init_points=20,
        n_iter=3,
    )

    policy = bd.SoftmaxPolicy()
    agent = bd.GradientAgent(bandit, policy, alpha=0.1, baseline=True, increase_rate=0)
    env = bd.Environment(bandit, agent, 'Gradient Agents', random_state=n*128)
    scores, actions = env.run(n_trials, file=file, stop_iter=100)
    
    return scores, actions

if os.path.exists('/home/xyz/data/haoyan/bandits/logs/rl_hybrid_results_shekel.txt'):
    os.remove('/home/xyz/data/haoyan/bandits/logs/rl_hybrid_results_shekel.txt')

with open('/home/xyz/data/haoyan/bandits/logs/rl_hybrid_results_shekel.txt', 'a') as file:
    res = [single_func(x, file) for x in range(n_experiment)]

0
|   iter    |  target   |     x     |     y     |
-------------------------------------------------
| 1         | 0.2964    | 4.798     | 5.712     |
| 2         | 0.3532    | 8.98      | 0.8659    |
| 3         | 0.2769    | 6.615     | 6.056     |
| 4         | 0.1287    | 2.243     | 9.72      |
| 5         | 0.3074    | 9.421     | 0.7115    |
| 6         | 0.2836    | 8.885     | 4.348     |
| 7         | 0.1905    | 0.4533    | 3.877     |
| 8         | 0.2238    | 8.696     | 6.078     |
| 9         | 0.3293    | 4.889     | 5.189     |
| 10        | 0.1433    | 6.465     | 9.719     |
| 11        | 0.4664    | 7.767     | 2.185     |
| 12        | 0.2061    | 7.483     | 7.314     |
| 13        | 0.3259    | 5.849     | 5.371     |
| 14        | 0.3098    | 7.939     | 4.806     |
| 15        | 0.5049    | 5.52      | 1.46      |
| 16        | 0.1153    | 1.005     | 9.786     |
| 17        | 0.4596    | 7.629     | 2.626     |
| 18        | 0.4568    | 6.218     | 3.679     

In [5]:
scores_list = []
actions_list = []
for x in res:
    scores_list.append(x[0])
    actions_list.append(x[1])
    
for scores, actions in zip(scores_list, actions_list):
    print(actions[np.argmax(scores)], scores[np.argmax(scores)], len(actions))

NameError: name 'res' is not defined

In [13]:
import os
import numpy as np
import scipy.stats as stats

from sklearn.model_selection import ParameterSampler, ParameterGrid


# specify parameters and distributions to sample from
params_list_dict = {
    'u': vec,
    'v': vec,
    'x': stats.uniform(bound[0], bound[1]),
    'y': stats.uniform(bound[0], bound[1]),
}

# n_iter = max([len(actions) for actions in actions_list])
n_iter = 100000
n_experiment = 5

res_dict_list = []
if os.path.exists('/home/xyz/data/haoyan/bandits/logs/grid_search_results_shekel.txt'):
    os.remove('/home/xyz/data/haoyan/bandits/logs/grid_search_results_shekel.txt')

with open('/home/xyz/data/haoyan/bandits/logs/grid_search_results_shekel.txt', 'a') as file:
    for n in range(n_experiment):
        param_list = list(ParameterSampler(params_list_dict, n_iter=n_iter, random_state=n*128))
        res_dict = {}
        for i, param in enumerate(param_list):
            res_dict[str(param)] = g(**param)
            file.write(f'({n*128}, {i}, {param}, {res_dict[str(param)]})\n')
            
        res_dict_list.append(res_dict)

In [15]:
from bayes_opt import BayesianOptimization
from bayes_opt.logger import JSONLogger
from bayes_opt.event import Events

def g_hat(u, v, x, y):
    return g(
        int(int(u)),
        int(int(v)),
        x,
        y
    )


pbounds = {
    'u': (0, 10),
    'v': (0, 10),
    'x': (0, 10),
    'y': (0, 10),
}


def single_experiment(n):
    optimizer = BayesianOptimization(
        f=g_hat,
        pbounds=pbounds,
        random_state=n,
        allow_duplicate_points=False
    )

    logger = JSONLogger(path=f"/home/xyz/data/haoyan/bandits/logs/bayesian_results_shekel_{n*128}.log")
    optimizer.subscribe(Events.OPTIMIZATION_STEP, logger)

    optimizer.maximize(init_points=1, n_iter=750)
    return optimizer.max
    
from multiprocessing import Pool


n_experiment = 5
param_list = list(range(n_experiment))
with Pool(5) as p:
    b_res_list = p.map(single_experiment, param_list)
    
# for n in range(n_experiment):
#     optimizer = BayesianOptimization(
#         f=g_hat,
#         pbounds=pbounds,
#         random_state=n,
#         allow_duplicate_points=True
#     )

#     optimizer.maximize(init_points=4, n_iter=500)
#     b_res_list.append(optimizer.max)

In [5]:
n_trials = 4000

params_list_dict = {
    'u': range(0, 11),
    'v': range(0, 11),
    'x': np.linspace(0, 10, 100),
    'y': np.linspace(0, 10, 100),
}

def single_func(n, file):
    bandit = bd.GaussianBanditOri(
        g,
        params_list_dict=params_list_dict,
    )

    policy = bd.SoftmaxPolicy()
    agent = bd.GradientAgent(bandit, policy, alpha=0.1, baseline=True, increase_rate=0)
    env = bd.Environment(bandit, agent, 'Gradient Agents', random_state=n*128)
    scores, actions = env.run(n_trials, file=file, stop_iter=100)
    
    return scores, actions

if os.path.exists('/home/xyz/data/haoyan/bandits/logs/rl_results_shekel.txt'):
    os.remove('/home/xyz/data/haoyan/bandits/logs/rl_results_shekel.txt')

with open('/home/xyz/data/haoyan/bandits/logs/rl_results_shekel.txt', 'a') as file:
    res = [single_func(x, file) for x in range(n_experiment)]
    

0
0.24556776608922432
0.1
((6, 0, 4.040404040404041, 6.4646464646464645), None) 0.24556776608922432
1
0.3198456035070681
0.1
((7, 9, 5.353535353535354, 7.979797979797979), None) 0.3198456035070681
2
0.33092741058282615
0.1
((6, 6, 9.393939393939394, 4.343434343434343), None) 0.33092741058282615
3
0.12437170012438079
0.1
((5, 10, 9.393939393939394, 0.8080808080808081), None) 0.12437170012438079
4
0.29769319011553913
0.1
((4, 7, 2.6262626262626263, 2.2222222222222223), None) 0.29769319011553913
5
0.2517022858281661
0.1
((7, 1, 1.5151515151515151, 3.131313131313131), None) 0.2517022858281661
6
0.2051421831241788
0.1
((4, 8, 9.494949494949495, 8.080808080808081), None) 0.2051421831241788
7
0.23313750374868092
0.1
((9, 8, 9.09090909090909, 4.545454545454545), None) 0.23313750374868092
8
0.2647969776604041
0.1
((10, 6, 6.0606060606060606, 3.131313131313131), None) 0.2647969776604041
9
0.37407024542119627
0.1
((4, 2, 3.9393939393939394, 6.4646464646464645), None) 0.37407024542119627
10
0.7222

our hybrid optimization method takes advantage of reinforcement learning to handle the discrete parameters, which successfully reduces the dimension of the parameter space for Bayesian Optimization. The technique improves the accuracy
of the solutions, compared with Bayesian Optimization and Random Search. The overhead of the one step Bayesian Optimization
is overcomed by highly reducing the iteration steps of Bayesian Optimization in the hybrid method because of the 
dimension reduction. The overall iteration steps is also compressed compared with Random Search to reach the global
minimizer.